In [27]:
import Pkg; Pkg.add(Pkg.PackageSpec(url="https://github.com/JuliaComputing/JuliaAcademyData.jl"))
using JuliaAcademyData; activate("Parallel_Computing")

   Updating git-repo `https://github.com/JuliaComputing/JuliaAcademyData.jl`


Fetching: [========================================>]  100.0 %Fetching: [======================>                  ]  54.7 %Fetching: [========================>                ]  58.8 %Fetching: [=========================>               ]  62.2 %Fetching: [==========================>              ]  64.9 %Fetching: [============================>            ]  68.2 %Fetching: [=============================>           ]  70.9 %Fetching: [==============================>          ]  73.6 %Fetching: [===============================>         ]  76.4 %Fetching: [================================>        ]  78.4 %Fetching: [=================================>       ]  81.1 %Fetching: [==================================>      ]  83.8 %Fetching: [===================================>     ]  86.5 %Fetching: [====================================>    ]  89.2 %Fetching: [=====================================>   ]  91.9 %Fetching: [======================================>  ]  94.6 %Fetching: [============

   Updating registry at `~/.julia/registries/JuliaComputingRegistry`
  Resolving package versions...


LoadError: expected package `Libtiff_jll [89763e89]` to be registered



# Julia is fast

Very often, benchmarks are used to compare languages.  These benchmarks can
lead to long discussions, first as to exactly what is being benchmarked and
secondly what explains the differences.  These simple questions can sometimes
get more complicated than you at first might imagine.

The purpose of this notebook is for you to see a simple benchmark for
yourself.

(This material began life as a wonderful lecture by Steven Johnson at MIT:
[Boxes and registers](https://github.com/stevengj/18S096/blob/master/lectures/lecture1/Boxes-and-registers.ipynb)).

# Outline of this notebook

- Define the sum function
- Implementations & benchmarking of sum in...
    - Julia (built-in)
    - Julia (hand-written)
    - C (hand-written)
    - python (built-in)
    - python (numpy)
    - python (hand-written)
- Towards exploiting parallelism with Julia
    - Allowing for floating point associativity
    - Making use of four cores at once: built-in
    - Making use of four cores at once: hand-written
- Summary of benchmarks

# `sum`: An easy enough function to understand

Consider the  **sum** function `sum(a)`, which computes
$$
\mathrm{sum}(a) = \sum_{i=1}^n a_i,
$$
where $n$ is the length of `a`.

In [1]:
a = rand(10^7) # 1D vector of random numbers, uniform on [0,1)

10000000-element Array{Float64,1}:
 0.2664603300590509
 0.6851890224563133
 0.23591825770449204
 0.5531037185435657
 0.9615313145348341
 0.08890278427471321
 0.5557010621980059
 0.011848151483493607
 0.1467816025248485
 0.9917819375543271
 0.6042627129089588
 0.5078094234211925
 0.8469791910016224
 ⋮
 0.7298278463261949
 0.580156339496116
 0.6009106816895964
 0.941567621010966
 0.97805312567953
 0.4647405011406287
 0.1964548718343373
 0.548694074284547
 0.5328231912514845
 0.8444528960484385
 0.034851732465528196
 0.6968866135787515

In [2]:
sum(a)

5.000595283622526e6

The expected result is ~0.5 * 10^7, since the mean of each entry is 0.5

# Benchmarking a few ways in a few languages

In [7]:
@time sum(a)

  0.004563 seconds (1 allocation: 16 bytes)


5.000595283622526e6

In [8]:
@time sum(a)

  0.004798 seconds (1 allocation: 16 bytes)


5.000595283622526e6

In [9]:
@time sum(a)

  0.004527 seconds (1 allocation: 16 bytes)


5.000595283622526e6

In [10]:
4.999967602718601e6 ≈ 4999967.6

true

###### The `@time` macro can yield noisy results, so it's not our best choice for benchmarking!

Luckily, Julia has a `BenchmarkTools.jl` package to make benchmarking easy and accurate:

In [11]:
using BenchmarkTools

In [12]:
@benchmark sum($a)

BenchmarkTools.Trial: 
  memory estimate:  0 bytes
  allocs estimate:  0
  --------------
  minimum time:     4.229 ms (0.00% GC)
  median time:      4.849 ms (0.00% GC)
  mean time:        4.814 ms (0.00% GC)
  maximum time:     6.122 ms (0.00% GC)
  --------------
  samples:          1039
  evals/sample:     1


# 1. Julia Built-in

So that's the performance of Julia's built-in sum — but that could be doing any number of tricks to be fast, including not using Julia at all in the first place! Of course, it is indeed written in Julia, but would it perform if we write a naive implementation ourselves?

In [13]:
@which sum(a)

sum(a::AbstractArray; dims) in Base at reducedim.jl:722

Let's save these benchmark results to a dictionary so we can start keeping track of them and comparing them down the line.

In [14]:
j_bench = @benchmark sum($a)

BenchmarkTools.Trial: 
  memory estimate:  0 bytes
  allocs estimate:  0
  --------------
  minimum time:     4.173 ms (0.00% GC)
  median time:      5.058 ms (0.00% GC)
  mean time:        5.056 ms (0.00% GC)
  maximum time:     7.029 ms (0.00% GC)
  --------------
  samples:          989
  evals/sample:     1

In [15]:
d = Dict()
d["Julia built-in"] = minimum(j_bench.times) / 1e6
d

Dict{Any,Any} with 1 entry:
  "Julia built-in" => 4.17313

# 2. Julia (hand-written)

In [16]:
function mysum(A)
    s = 0.0
    for a in A
        s += a
    end
    return s
end

mysum (generic function with 1 method)

In [17]:
j_bench_hand = @benchmark mysum($a)

BenchmarkTools.Trial: 
  memory estimate:  0 bytes
  allocs estimate:  0
  --------------
  minimum time:     10.409 ms (0.00% GC)
  median time:      11.712 ms (0.00% GC)
  mean time:        11.698 ms (0.00% GC)
  maximum time:     12.763 ms (0.00% GC)
  --------------
  samples:          428
  evals/sample:     1

In [18]:
d["Julia hand-written"] = minimum(j_bench_hand.times) / 1e6
d

Dict{Any,Any} with 2 entries:
  "Julia hand-written" => 10.4089
  "Julia built-in"     => 4.17313

So that's about 2x slower than the builtin definition. We'll see why later on.

But first: is this fast?  How would we know?  Let's compare it to some other languages...

#  3. The C language

C is often considered the gold standard: difficult on the human, nice for the machine. Getting within a factor of 2 of C is often satisfying. Nonetheless, even within C, there are many kinds of optimizations possible that a naive C writer may or may not get the advantage of.

The current author does not speak C, so he does not read the cell below, but is happy to know that you can put C code in a Julia session, compile it, and run it. Note that the `"""` wrap a multi-line string.

In [19]:
using Libdl
C_code = """
    #include <stddef.h>
    double c_sum(size_t n, double *X) {
        double s = 0.0;
        for (size_t i = 0; i < n; ++i) {
            s += X[i];
        }
        return s;
    }
"""

const Clib = tempname()   # make a temporary file


# compile to a shared library by piping C_code to gcc
# (works only if you have gcc installed):

open(`gcc -fPIC -O3 -msse3 -xc -shared -o $(Clib * "." * Libdl.dlext) -`, "w") do f
    print(f, C_code)
end

# define a Julia function that calls the C function:
c_sum(X::Array{Float64}) = ccall(("c_sum", Clib), Float64, (Csize_t, Ptr{Float64}), length(X), X)

c_sum (generic function with 1 method)

In [20]:
c_sum(a)

5.000595283622347e6

In [21]:
c_sum(a) ≈ sum(a) # type \approx and then <TAB> to get the ≈ symbolb

true

We can now benchmark the C code directly from Julia:

In [22]:
c_bench = @benchmark c_sum($a)

BenchmarkTools.Trial: 
  memory estimate:  0 bytes
  allocs estimate:  0
  --------------
  minimum time:     11.206 ms (0.00% GC)
  median time:      11.723 ms (0.00% GC)
  mean time:        11.714 ms (0.00% GC)
  maximum time:     15.189 ms (0.00% GC)
  --------------
  samples:          427
  evals/sample:     1

In [23]:
d["C"] = minimum(c_bench.times) / 1e6  # in milliseconds
d

Dict{Any,Any} with 3 entries:
  "C"                  => 11.2062
  "Julia hand-written" => 10.4089
  "Julia built-in"     => 4.17313

# 4. Python's built in `sum`

The `PyCall` package provides a Julia interface to Python:

In [24]:
using PyCall

In [25]:
# get the Python built-in "sum" function:
pysum = pybuiltin("sum")

PyObject <built-in function sum>

In [26]:
pysum(a)

5.000595283622347e6

In [27]:
pysum(a) ≈ sum(a)

true

In [28]:
py_list_bench = @benchmark $pysum($a)

BenchmarkTools.Trial: 
  memory estimate:  336 bytes
  allocs estimate:  6
  --------------
  minimum time:     1.361 s (0.00% GC)
  median time:      1.383 s (0.00% GC)
  mean time:        1.381 s (0.00% GC)
  maximum time:     1.398 s (0.00% GC)
  --------------
  samples:          4
  evals/sample:     1

In [30]:
d["Python built-in"] = minimum(py_list_bench.times) / 1e6
d

Dict{Any,Any} with 4 entries:
  "C"                  => 11.2062
  "Julia hand-written" => 10.4089
  "Julia built-in"     => 4.17313
  "Python built-in"    => 1360.75

# 5. Python: `numpy`

`numpy` is an optimized C library, callable from Python.
It may be installed within Julia as follows:

In [31]:
using Conda

In [32]:
# Conda.add("numpy")

In [33]:
numpy_sum = pyimport("numpy")["sum"]

py_numpy_bench = @benchmark $numpy_sum($a)

BenchmarkTools.Trial: 
  memory estimate:  336 bytes
  allocs estimate:  6
  --------------
  minimum time:     3.600 ms (0.00% GC)
  median time:      3.774 ms (0.00% GC)
  mean time:        3.883 ms (0.00% GC)
  maximum time:     7.507 ms (0.00% GC)
  --------------
  samples:          1287
  evals/sample:     1

In [34]:
numpy_sum(a)

5.000595283622524e6

In [35]:
numpy_sum(a) ≈ sum(a)

true

In [36]:
d["Python numpy"] = minimum(py_numpy_bench.times) / 1e6
d

Dict{Any,Any} with 5 entries:
  "C"                  => 11.2062
  "Julia hand-written" => 10.4089
  "Python numpy"       => 3.59995
  "Julia built-in"     => 4.17313
  "Python built-in"    => 1360.75

# 6. Python, hand-written

In [37]:
py"""
def py_sum(A):
    s = 0.0
    for a in A:
        s += a
    return s
"""

sum_py = py"py_sum"

PyObject <function py_sum at 0x7fadd4e1e7b8>

In [38]:
py_hand = @benchmark $sum_py($a)

BenchmarkTools.Trial: 
  memory estimate:  336 bytes
  allocs estimate:  6
  --------------
  minimum time:     1.672 s (0.00% GC)
  median time:      1.716 s (0.00% GC)
  mean time:        1.721 s (0.00% GC)
  maximum time:     1.776 s (0.00% GC)
  --------------
  samples:          3
  evals/sample:     1

In [39]:
sum_py(a)

5.000595283622347e6

In [40]:
sum_py(a) ≈ sum(a)

true

In [42]:
d["Python hand-written"] = minimum(py_hand.times) / 1e6
d

Dict{Any,Any} with 6 entries:
  "C"                   => 11.2062
  "Julia hand-written"  => 10.4089
  "Python numpy"        => 3.59995
  "Python hand-written" => 1672.18
  "Julia built-in"      => 4.17313
  "Python built-in"     => 1360.75

# Summary so far

In [43]:
for (key, value) in sort(collect(d), by=last)
    println(rpad(key, 25, "."), lpad(round(value; digits=1), 6, "."))
end

Python numpy................3.6
Julia built-in..............4.2
Julia hand-written.........10.4
C..........................11.2
Python built-in..........1360.8
Python hand-written......1672.2


We seem to have three different performance classes here: The numpy and Julia
builtins are leading the pack, followed by the hand-written Julia and C
definitions. Those seem to be about 2x slower.  And then we have the much much
slower Python definitions over 100x slower.

# Exploiting parallelism with Julia

The fact that our hand-written Julia solution was almost an even multiple of
2x slower than the builtin solutions is a big clue: perhaps theres some sort
of 2x parallelism going on here?

(In fairness, there are ways to exploit parallelism in other languages, too,
but for brevity we won't cover them)

# 7. Julia (allowing floating point associativity)

The `for` loop

```julia
for a in A
    s += a
end
```

defines a very strict _order_ to the summation: Julia follows exactly what you
wrote and adds the elements of `A` to the result `s` in the order it iterates.
Since floating point numbers aren't associative, a rearrangement here would
change the answer — and Julia is loathe to give you different answer than
the one you asked for.

You can, however, tell Julia to relax that rule and allow for associativity
with the `@fastmath` macro. This might allow Julia to rearrange the sum in an
advantageous manner.

In [44]:
function mysum_fast(A)
    s = 0.0
    for a in A
        @fastmath s += a
    end
    s
end

mysum_fast (generic function with 1 method)

In [45]:
j_bench_hand_fast = @benchmark mysum_fast($a)

BenchmarkTools.Trial: 
  memory estimate:  0 bytes
  allocs estimate:  0
  --------------
  minimum time:     4.122 ms (0.00% GC)
  median time:      4.812 ms (0.00% GC)
  mean time:        4.829 ms (0.00% GC)
  maximum time:     6.234 ms (0.00% GC)
  --------------
  samples:          1036
  evals/sample:     1

In [46]:
mysum_fast(a)

5.000595283622536e6

In [47]:
d["Julia hand-written fast"] = minimum(j_bench_hand_fast.times) / 1e6
d

Dict{Any,Any} with 7 entries:
  "C"                       => 11.2062
  "Julia hand-written"      => 10.4089
  "Python numpy"            => 3.59995
  "Python hand-written"     => 1672.18
  "Julia built-in"          => 4.17313
  "Python built-in"         => 1360.75
  "Julia hand-written fast" => 4.12174

# 8. Distributed Julia (built-in)

We can take this one step further: nearly every modern computer these days has
multiple cores. All the above solutions are working one core hard, but all the
others are just sitting by idly. Let's put them to work!

In [48]:
using Distributed
using DistributedArrays
addprocs(4)
@sync @everywhere workers() include("/opt/julia-1.0/etc/julia/startup.jl") # Needed just for JuliaBox
@everywhere using DistributedArrays

┌ Info: Precompiling DistributedArrays [aaf54ef3-cdf8-58ed-94cc-d582ad619b94]
└ @ Base loading.jl:1278


In [49]:
adist = distribute(a)
j_bench_dist = @benchmark sum($adist)

BenchmarkTools.Trial: 
  memory estimate:  13.09 KiB
  allocs estimate:  348
  --------------
  minimum time:     3.107 ms (0.00% GC)
  median time:      4.430 ms (0.00% GC)
  mean time:        4.337 ms (0.00% GC)
  maximum time:     8.114 ms (0.00% GC)
  --------------
  samples:          1152
  evals/sample:     1

In [50]:
d["Julia 4x built-in"] = minimum(j_bench_dist.times) / 1e6
d

Dict{Any,Any} with 8 entries:
  "C"                       => 11.2062
  "Julia hand-written"      => 10.4089
  "Python numpy"            => 3.59995
  "Python hand-written"     => 1672.18
  "Julia built-in"          => 4.17313
  "Python built-in"         => 1360.75
  "Julia 4x built-in"       => 3.10721
  "Julia hand-written fast" => 4.12174

# 9. Distributed Julia (hand-written)

Ok, that might be cheating, too — it's again just calling a library
function. Is it possible to write distributed sum ourselves?

In [51]:
function mysum_dist(a::DArray)
    r = Array{Future}(undef, length(procs(a)))
    for (i, id) in enumerate(procs(a))
        r[i] = @spawnat id sum(localpart(a))
    end
    return sum(fetch.(r))
end

mysum_dist (generic function with 1 method)

In [52]:
j_bench_hand_dist = @benchmark mysum_dist($adist)

BenchmarkTools.Trial: 
  memory estimate:  19.19 KiB
  allocs estimate:  533
  --------------
  minimum time:     3.191 ms (0.00% GC)
  median time:      4.537 ms (0.00% GC)
  mean time:        4.540 ms (0.00% GC)
  maximum time:     7.754 ms (0.00% GC)
  --------------
  samples:          1101
  evals/sample:     1

In [54]:
d["Julia 4x hand-written"] = minimum(j_bench_hand_dist.times) / 1e6
d

Dict{Any,Any} with 9 entries:
  "C"                       => 11.2062
  "Julia hand-written"      => 10.4089
  "Python numpy"            => 3.59995
  "Python hand-written"     => 1672.18
  "Julia built-in"          => 4.17313
  "Python built-in"         => 1360.75
  "Julia 4x built-in"       => 3.10721
  "Julia 4x hand-written"   => 3.1905
  "Julia hand-written fast" => 4.12174

# Overall Summary

In [55]:
for (key, value) in sort(collect(d), by=last)
    println(rpad(key, 25, "."), lpad(round(value; digits=1), 6, "."))
end

Julia 4x built-in...........3.1
Julia 4x hand-written.......3.2
Python numpy................3.6
Julia hand-written fast.....4.1
Julia built-in..............4.2
Julia hand-written.........10.4
C..........................11.2
Python built-in..........1360.8
Python hand-written......1672.2


# Key take-aways

* Julia allows for serial C-like performance, even with hand-written functions
* Julia allows us to exploit many forms of parallelism to further improve performance. We demonstrated:
    * Single-processor parallelism with SIMD
    * Multi-process parallelism with DistributedArrays
* But there are many other ways to express parallelism, too!